In [2]:
import torch
import torch.nn as nn
from torch import optim
import polars as pl
import pandas as pd
import ta
import numpy as np
import torch
import math
import plotly.graph_objects as go
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from sklearn.preprocessing import StandardScaler

In [3]:
TEST_SIZE = 5000
TS_LEN = 12

In [4]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size=122, hidden_size=256):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size, num_layers=2, batch_first=True, dropout=0.2)

    def forward(self, input):
        out = self.fc1(input)
        output, hidden = self.gru(out)
        return output, hidden


In [5]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size=256, output_size=122, max_length=32):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.max_length = max_length

        self.gru = nn.GRU(output_size, self.hidden_size, num_layers=2, batch_first=True, dropout=0.2)
        self.out = nn.Linear(self.hidden_size, output_size)

    def forward(self, input, hidden, encoder_outputs):
        output, hidden = self.gru(input, hidden)
        x = self.out(output)
        return x, hidden


In [6]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size=256, output_size=122, max_length=32):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.max_length = max_length

        self.attn = nn.Linear(self.hidden_size * 2, hidden_size)
        self.v = nn.Linear(self.hidden_size, 1)
        self.gru = nn.GRU(self.hidden_size+self.output_size, self.hidden_size, num_layers=2, batch_first=True, dropout=0.2)
        self.out = nn.Linear(self.hidden_size*2, output_size)

    def forward(self, input, hidden, encoder_outputs):
        
        last_hidden = hidden[-1, :, :].unsqueeze(0).permute(1, 0, 2)
        energy = torch.tanh(
            self.attn(torch.cat((last_hidden.repeat(1, 8 , 1), encoder_outputs), dim = 2))
        )
        attn_weights = self.v(energy).squeeze(2)
        attn_weights = F.softmax(attn_weights, dim=1).unsqueeze(1)
        
        attn_applied = torch.bmm( 
            attn_weights, encoder_outputs
        )
        gru_input = torch.cat((input, attn_applied), dim = 2)
        output, hidden_out = self.gru(gru_input, hidden)
        output = torch.tanh(output)
        #attn_applied = attn_applied.squeeze(1)
        x = self.out(torch.cat((output, attn_applied), dim = 2))
        return x, hidden_out


In [7]:
import random


class Seq2seq(nn.Module):
    def __init__(self, encoder, decoder, device):
        super(Seq2seq, self).__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.device = device
       

    def forward(self, input_seq, prev, features):
        batch = input_seq.shape[0]
        encoder_outputs, hidden = self.encoder(input_seq)
        input = prev#input_seq[:, 1, 64]
        output_seq_len = 4
        outputs = []

        for i in range(output_seq_len):
            output, hidden = self.decoder(input, hidden, encoder_outputs)
            outputs.append(output[:, :, 0:1])
            if i+1 < output_seq_len:
                input = torch.cat([output[:, :, 0:1],features[:, i:i+1, 1:]], dim=2) 

        return torch.stack(outputs).view(batch, 4, 1)

In [8]:
pl_df = pl.read_parquet("./ETHUSDT_FEATURES_DATASET_136_23032023.parquet")
pl_df.head()[:, 64]

shape: (5,)
Series: 'close' [f64]
[
	1568.75
	1568.47
	1569.42
	1570.0
	1567.93
]

In [9]:
X = pl_df.select(pl.exclude(["time"]))[:-4].to_pandas()

rsi_2 = ta.momentum.RSIIndicator(close = X.close, window = 2)
rsi_5 = ta.momentum.RSIIndicator(close = X.close, window = 5)
rsi_10 = ta.momentum.RSIIndicator(close = X.close, window = 10)
rsi_20 = ta.momentum.RSIIndicator(close = X.close, window = 20)
X["RSI_5"] = rsi_5.rsi()
X["RSI_10"] = rsi_10.rsi()
X["RSI_20"] = rsi_20.rsi()

X["MACD_2"] = ta.trend.macd(X.close, window_slow = 5, window_fast = 2)
X["MACD_5"] = ta.trend.macd(X.close, window_slow = 10, window_fast = 5)
X["MACD_10"] = ta.trend.macd(X.close, window_slow = 20, window_fast = 10)
X["MACD_15"] = ta.trend.macd(X.close, window_slow = 15, window_fast = 10)

X["ADI"] = ta.volume.AccDistIndexIndicator(high = X.high, low = X.low, close = X.close, volume=X.volume).acc_dist_index()

X["ADX_2"] = ta.trend.ADXIndicator(high = X.high, low = X.low, close = X.close, window=2).adx() 
X["ADX_4"] = ta.trend.ADXIndicator(high = X.high, low = X.low, close = X.close, window=4).adx() 
X["ADX_8"] = ta.trend.ADXIndicator(high = X.high, low = X.low, close = X.close, window=8).adx() 

X["FII_2"] = ta.volume.ForceIndexIndicator(close = X.close, volume=X.volume, window = 2).force_index() 
X["FII_4"] = ta.volume.ForceIndexIndicator(close = X.close, volume=X.volume, window = 4).force_index() 
X["FII_8"] = ta.volume.ForceIndexIndicator(close = X.close, volume=X.volume, window = 8).force_index() 

X["SR_2"] = ta.momentum.StochasticOscillator(high = X.high, low = X.low, close = X.close, window = 2).stoch()
X["SR_4"] = ta.momentum.StochasticOscillator(high = X.high, low = X.low, close = X.close, window = 4).stoch()
X["SR_8"] = ta.momentum.StochasticOscillator(high = X.high, low = X.low, close = X.close, window = 8).stoch()

X["roc_2"] = ta.momentum.ROCIndicator(X.close, 2).roc()
X["roc_4"] = ta.momentum.ROCIndicator(X.close, 4).roc()
X["roc_8"] = ta.momentum.ROCIndicator(X.close, 8).roc()
X["roc_12"] = ta.momentum.ROCIndicator(X.close, 12).roc()

X["roc_v_2"] = ta.momentum.ROCIndicator(X.volume, 2).roc()
X["roc_v_4"] = ta.momentum.ROCIndicator(X.volume, 4).roc()
X["roc_v_8"] = ta.momentum.ROCIndicator(X.volume, 8).roc()
X["roc_v_12"] = ta.momentum.ROCIndicator(X.volume, 12).roc()

X["roc_buy_volume_sum_5_10"] = X.buy_volume_sum_5 - X.buy_volume_sum_10
X["roc_buy_volume_sum_5_30"] = X.buy_volume_sum_5 - X.buy_volume_sum_30
X["roc_buy_volume_sum_10_30"] = X.buy_volume_sum_10 - X.buy_volume_sum_30
X["roc_buy_volume_sum_10_60"] = X.buy_volume_sum_10 - X.buy_volume_sum_60
X["roc_buy_volume_sum_30_60"] = X.buy_volume_sum_30 - X.buy_volume_sum_60

X["roc_sell_volume_sum_5_10"] = X.sell_volume_sum_5 - X.sell_volume_sum_10
X["roc_sell_volume_sum_5_30"] = X.sell_volume_sum_5 - X.sell_volume_sum_30
X["roc_sell_volume_sum_10_30"] = X.sell_volume_sum_10 - X.sell_volume_sum_30
X["roc_sell_volume_sum_10_60"] = X.sell_volume_sum_10 - X.sell_volume_sum_60
X["roc_sell_volume_sum_30_60"] = X.sell_volume_sum_30 - X.sell_volume_sum_60

X["roc_buy_volume_std_5_10"] = X.buy_volume_std_5 - X.buy_volume_std_10
X["roc_buy_volume_std_5_30"] = X.buy_volume_std_5 - X.buy_volume_std_30
X["roc_buy_volume_std_10_30"] = X.buy_volume_std_10 - X.buy_volume_std_30
X["roc_buy_volume_std_10_60"] = X.buy_volume_std_10 - X.buy_volume_std_60
X["roc_buy_volume_std_30_60"] = X.buy_volume_std_30 - X.buy_volume_std_60

X["roc_sell_volume_std_5_10"] = X.sell_volume_std_5 - X.sell_volume_std_10
X["roc_sell_volume_std_5_30"] = X.sell_volume_std_5 - X.sell_volume_std_30
X["roc_sell_volume_std_10_30"] = X.sell_volume_std_10 - X.sell_volume_std_30
X["roc_sell_volume_std_10_60"] = X.sell_volume_std_10 - X.sell_volume_std_60
X["roc_sell_volume_std_30_60"] = X.sell_volume_std_30 - X.sell_volume_std_60

data_y = pd.DataFrame()
data_y['target'] = pl_df[:-3,['close']].to_pandas()
##data_y['target'] = ta.trend.SMAIndicator(pl_df.to_pandas().close, window = 4).sma_indicator()[3:-1].reset_index(drop=True)
y = pd.DataFrame()

y['target'] = data_y['target']

X.replace([np.inf, -np.inf], np.nan, inplace=True)
X.replace(np.nan, 0.0, inplace=True)
X = X[20:].reset_index(drop=True)
y = y[20:].reset_index(drop=True)
print(X.shape)

/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:785: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:785: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py

(195796, 122)


In [10]:

col = X.pop('close')
X.insert(0, 'close', col)

In [11]:
data_x = X.values.tolist()
feature_scaler = StandardScaler()
feature_scaler.fit(data_x)
data_x = feature_scaler.transform(data_x)

In [12]:
dataset_x = []
dataset_y = []
backtest_close = []
for i in range(TS_LEN, len(data_x)+1):
    dataset_x.append(data_x[i-TS_LEN: i-4])
    dataset_y.append(data_x[i-4: i])
    backtest_close.append(data_x[i-2])
    #dataset_y.append(data_x[i-TS_LEN+1: i+1])

In [13]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

X_test_df = dataset_x[-50000:-20000]
X_train_df = dataset_x[:-50000]

y_test_df = dataset_y[-50000:-20000]
backtest_close = backtest_close[-50000:-20000]
y_train_df = dataset_y[:-50000]
device

device(type='cuda')

In [14]:

class TimeSeriesDataset(Dataset):
    def __init__(self, x, y):
        #x = np.expand_dims(x, 2)
        self.x = x.astype(np.float32)
        self.y = y.astype(np.float32)
        
    def __len__(self):
        return len(self.x)

    def __getitem__(self, idx):
        return (self.x[idx], self.y[idx])

dataset_train = TimeSeriesDataset(np.array(X_train_df), np.array(y_train_df))
dataset_val = TimeSeriesDataset(np.array(X_test_df), np.array(y_test_df))

print("Train data shape", dataset_train.x.shape, dataset_train.y.shape)
print("Validation data shape", dataset_val.x.shape, dataset_val.y.shape)

Train data shape (145785, 8, 122) (145785, 4, 122)
Validation data shape (30000, 8, 122) (30000, 4, 122)


In [15]:
train_dataloader = DataLoader(dataset_train, batch_size=1, shuffle=True)
val_dataloader = DataLoader(dataset_val, batch_size=1, shuffle=False)
test_dataloader = DataLoader(dataset_val, batch_size=1, shuffle=False)

In [16]:
encoder = EncoderRNN()
#decoder = AttnDecoderRNN()
decoder = DecoderRNN()
model = Seq2seq(encoder, decoder, device).to(device)
model

Seq2seq(
  (encoder): EncoderRNN(
    (fc1): Linear(in_features=122, out_features=256, bias=True)
    (gru): GRU(256, 256, num_layers=2, batch_first=True, dropout=0.2)
  )
  (decoder): DecoderRNN(
    (gru): GRU(122, 256, num_layers=2, batch_first=True, dropout=0.2)
    (out): Linear(in_features=256, out_features=122, bias=True)
  )
)

In [ ]:
def init_weights(m):
    for name, param in m.named_parameters():
        nn.init.uniform_(param.data, -0.08, 0.08)
        
model.apply(init_weights)

In [ ]:
def run_epoch(dataloader, is_training=False):
    epoch_loss = 0

    if is_training:
        print("training ep...")
        model.train()
    else:
        print("eval ep...")
        model.eval()

    for idx, (x, y) in tqdm(enumerate(dataloader)):
        if is_training:
            optimizer.zero_grad()

        batchsize = x.shape[0]

        x = x.to(device)
        y = y.to(device)

        out = model(x, x[:, -1:, :], y[:, :-1, :])

        loss = criterion(out, y[:, :, 0:1])

        if is_training:
            loss.backward()
            optimizer.step()

        epoch_loss += (loss.detach().item() / batchsize)

    lr = scheduler.get_last_lr()[0]

    return epoch_loss/len(dataloader), lr

LR = 0.001
STEP_SIZE = 4
EPOCHS = 10

criterion = nn.MSELoss(reduction="sum")
optimizer = optim.Adam(model.parameters(), lr=LR, betas=(0.9, 0.98), eps=1e-9)
scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=STEP_SIZE, gamma=0.1)


for epoch in range(EPOCHS):
    loss_train, lr_train = run_epoch(train_dataloader, is_training=True)
    loss_val, lr_val = run_epoch(val_dataloader)
    scheduler.step()
    
    print('Epoch[{}/{}] | loss train:{:.6f}, test:{:.6f} | lr:{:.6f}'
              .format(epoch+1, EPOCHS, loss_train, loss_val, lr_train))

In [ ]:
#torch.save(model, "PATH_TO_MODEL")

In [17]:
model = torch.load("PATH_TO_MODEL").to(device)

In [18]:
def predict(dataloader):
    model.eval()
    predictions = []
    targets = []
    i = 0
    for idx, (x, y) in enumerate(dataloader):
        batchsize = x.shape[0]
        x = x.to(device)
        y = y.to(device)
        out = model(x, x[:, -1:, :], y[:, :-1, :])
        targets.append([y[0, -1, 0].item()])
        predictions.append([out[0, -1, 0].item()])

    #return target_scaler.inverse_transform(predictions), target_scaler.inverse_transform(targets)
    return predictions, targets
pred, targ = predict(test_dataloader)
pred = [row+[0]*121 for row in pred]
targ = [row+[0]*121 for row in targ]
pred, targ = feature_scaler.inverse_transform(pred), feature_scaler.inverse_transform(targ)
pred, targ = [row[0] for row in pred], [row[0] for row in targ]

In [19]:
fig = go.Figure()
fig.add_trace(go.Scatter(
                         y=pd.DataFrame(targ, dtype=float)[0],
                         mode='lines',
                         name='target',
                         line=dict(color='blue', width = 2)
                         ))
fig.add_trace(go.Scatter(
                         y=pd.DataFrame(pred, dtype=float)[0],
                         mode='lines',
                         name='predicted',
                         line=dict(color='red', width = 2)
                         ))
fig.show()

In [20]:
from sklearn.metrics import mean_absolute_percentage_error, mean_absolute_error, median_absolute_error, mean_squared_error
print(f"MSE: {mean_squared_error(targ, pred):.6f}")
print(f"MAE: {mean_absolute_error(targ, pred):.6f}")
print(f"MedAE: {median_absolute_error(targ, pred):.6f}")
print(f"MAPE: {mean_absolute_percentage_error(targ, pred):.6f}")

MSE: 2.694220
MAE: 0.998403
MedAE: 0.625710
MAPE: 0.000606


In [21]:
close = feature_scaler.inverse_transform(backtest_close)
close = [i[0] for i in close]

In [22]:
from backtest import MLBackTrader


test = MLBackTrader()
test.open_threshold = 3
test.load_predicted(pred)
test.load_target(close)
#test.maker_fee_multiplier = 0
#test.taker_fee_multiplier = 0
#test.spread_dummy = 0

In [23]:
test.run()

|31|
|OPEND SHORT POSITION | 1688.69
|CLOSE SHORT POSITION | 1684.36 | profit: 1.6493
|36|
|OPEND SHORT POSITION | 1683.08
|CLOSE SHORT POSITION | 1682.42 | profit: -0.18479
|68|
|OPEND SHORT POSITION | 1677.0
|CLOSE SHORT POSITION | 1679.32 | profit: -1.6736
|81|
|OPEND LONG POSITION | 1680.91
|CLOSE LONG POSITION | 1680.72 | profit: -0.60925
|549|
|OPEND SHORT POSITION | 1692.17
|CLOSE SHORT POSITION | 1694.57 | profit: -1.7181
|553|
|OPEND SHORT POSITION | 1707.04
|CLOSE SHORT POSITION | 1712.77 | profit: -3.3883
|555|
|OPEND SHORT POSITION | 1712.77
|CLOSE SHORT POSITION | 1715.22 | profit: -1.7493
|556|
|OPEND LONG POSITION | 1715.22
|CLOSE LONG POSITION | 1715.03 | profit: -0.61955
|557|
|OPEND SHORT POSITION | 1715.03
|CLOSE SHORT POSITION | 1717.69 | profit: -1.855
|558|
|OPEND SHORT POSITION | 1717.69
|CLOSE SHORT POSITION | 1727.16 | profit: -5.2622
|560|
|OPEND SHORT POSITION | 1727.16
|CLOSE SHORT POSITION | 1728.8 | profit: -1.3485
|571|
|OPEND SHORT POSITION | 1728.8
|CLO

In [24]:
test.plot()

In [25]:
import plotly.express as px


fig = px.line(x=test.portfolio_time, y=test.portfolio)
fig.update_layout(
    xaxis_title="Время (мин.)",
    yaxis_title="Портфолио",
)
fig.show()

In [26]:
print(f"Чистая прибыль: {sum(test.trade_profits):.2f}")
pos_prof_cnt = sum([1 if prof > 0 else 0 for prof in test.trade_profits])
neg_prof_cnt = sum([1 if prof < 0 else 0 for prof in test.trade_profits])
print(f"Процент прибыльных сделок: {pos_prof_cnt / len(test.trade_profits):.2f}")
print(f"Процент убыточных сделок: {neg_prof_cnt / len(test.trade_profits):.2f}")
print(f"Самая большая прибыльная сделка: {max(test.trade_profits):.2f}")
print(f"Самая большая убыточная сделка: {min(test.trade_profits):.2f}")
print(f"Средняя прибыльная сделка: {sum([prof if prof > 0 else 0 for prof in test.trade_profits]) / pos_prof_cnt:.2f}")
print(f"Средняя убыточная сделка: {sum([prof if prof < 0 else 0 for prof in test.trade_profits]) / neg_prof_cnt:.2f}")

Чистая прибыль: -5.15
Процент прибыльных сделок: 0.22
Процент убыточных сделок: 0.78
Самая большая прибыльная сделка: 24.68
Самая большая убыточная сделка: -6.90
Средняя прибыльная сделка: 4.39
Средняя убыточная сделка: -1.29
